In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [2]:
!pip install sentencepiece

     |████████████████████████████████| 1.2MB 8.1MB/s 


In [3]:
%%capture
!pip install transformers

In [4]:
import torch
import numpy as np
import pandas as pd
import torch.nn as nn

import transformers
from sklearn.metrics import *
from transformers import AdamW
from tqdm.notebook import tqdm
from scipy.special import softmax
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split as tts
from transformers import BertTokenizerFast, BertConfig, BertForSequenceClassification, AutoModel
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

In [5]:
# Define the device
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

#### Download

In [6]:
cd drive/My Drive/Colab Notebooks/experiments

/content/drive/My Drive/Colab Notebooks/experiments


In [7]:
# Download humor detection data
# Paper: https://arxiv.org/abs/2004.12765
data = pd.read_csv("data/trofix.csv")
print("\nThere are", len(data), "sentences")

# Use the standard text/label columns
# Create labels: 1 --> humorous, 0 --> not humorous
#data = data.dropna()
data["label"] = data["label"].apply(int)
data.head()


There are 1444 sentences


arg1     arg2  ... verb_stem label
0        mileage   struck  ...    strike     1
1      terrorist   attack  ...    attack     0
2         forces  stepped  ...      step     0
3            day     pour  ...      pour     0
4  manufacturers  rolling  ...      roll     1

[5 rows x 6 columns]

#### Split to training, validation and test



In [8]:
# Use a subset for quick experiments
#data = data[:10000]

# Split to train, val and test
train, test = tts(data[["sentence", "label"]], random_state=42, test_size=0.1)
train, val = tts(train, random_state=42, test_size=test.shape[0])

#### Tokenize and encode with BERT tokenizer

In [9]:
from transformers import XLMRobertaForSequenceClassification

output_dir = 'stockholm/xlm_code/trofix_xlmroberta/xlm-roberta_model_save'

print(output_dir)

stockholm/xlm_code/trofix_xlmroberta/xlm-roberta_model_save


In [10]:
from transformers import XLMRobertaTokenizer
import torch
# Load the BERT tokenizer.
print('Loading XLMRobertaTokenizer...')
bert_tokenizer = XLMRobertaTokenizer.from_pretrained(output_dir)
model_e = XLMRobertaForSequenceClassification.from_pretrained(output_dir, num_labels = 2, output_attentions = True, output_hidden_states = True,)

Loading XLMRobertaTokenizer...


Some weights of the model checkpoint at stockholm/xlm_code/trofix_xlmroberta/xlm-roberta_model_save were not used when initializing XLMRobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [11]:
MAX_LEN = 21 # This value could be set as 256, 512 etc.

encoded_instance = bert_tokenizer.encode_plus(
            train.iloc[0].sentence,
            truncation = True,                
            add_special_tokens = True,
            max_length = MAX_LEN,     
            pad_to_max_length = True,
            return_attention_mask = True,  
            return_tensors = 'pt' # return pytorch tensors
       )


encoded_instance

/usr/local/lib/python3.7/dist-packages/transformers/tokenization_utils_base.py:2132: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  FutureWarning,


{'input_ids': tensor([[     0,   9563,    237,  41325,    136,  10142,  17957,   3444,     47,
          59102,     10,  63847,    111,  43851,  36867,    242,      7, 181991,
             53,    390,      2]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [12]:
print("Original text:", train.iloc[0].sentence)
print("BERT BPEs:", bert_tokenizer.convert_ids_to_tokens(encoded_instance["input_ids"][0]))

Original text: Just as Reuters and Telerate want to grab a piece of Quotron 's territory by offering U.S. equities quotes , Quotron is eyeing their turf and mulling ways to offer pricing information on fixed-income instruments and foreign currencies .
BERT BPEs: ['<s>', '▁Just', '▁as', '▁Reuters', '▁and', '▁Tele', 'rate', '▁want', '▁to', '▁grab', '▁a', '▁piece', '▁of', '▁Quo', 'tron', "▁'", 's', '▁territor', 'y', '▁by', '</s>']


In [13]:
# Set max_len to the maximum length of the training data 
max_len = max([len(bert_tokenizer.encode(s)) for s in train.sentence.to_list()])
print("The maximum sentence length in training based on BERT BPEs is", max_len)

The maximum sentence length in training based on BERT BPEs is 121


In [14]:
# Tokenize and encode sentences in each set
x_train = bert_tokenizer.batch_encode_plus(
    train.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_val = bert_tokenizer.batch_encode_plus(
    val.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_test = bert_tokenizer.batch_encode_plus(
    test.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)

In [15]:
# Convert lists to tensors in order to feed them to our PyTorch model
train_seq = torch.tensor(x_train['input_ids'])
train_mask = torch.tensor(x_train['attention_mask'])
train_y = torch.tensor(train.label.tolist())

val_seq = torch.tensor(x_val['input_ids'])
val_mask = torch.tensor(x_val['attention_mask'])
val_y = torch.tensor(val.label.tolist())

test_seq = torch.tensor(x_test['input_ids'])
test_mask = torch.tensor(x_test['attention_mask'])
test_y = torch.tensor(test.label.tolist())

In [16]:
batch_size = 32

# Create a dataloader for each set

# TensorDataset: Creates a PyTorch dataset object to load data from
train_data = TensorDataset(train_seq, train_mask, train_y)
# RandomSampler: specify the sequence of indices/keys used in data loading
train_sampler = RandomSampler(train_data)
# DataLoader: a Python iterable over a dataset
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_seq, val_mask, val_y)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

test_data = TensorDataset(test_seq, test_mask, test_y)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=1)

## Inference

#### Load the saved checkpoint

In [17]:
model_e = model_e.to(device)

#### Get predictions for test

In [18]:
# Predict for the test set and save the results
model_e.eval()
test_predictions = []
test_targets = []
test_attentions = []
test_inputs = []

for batch in test_dataloader:
  batch = [t.to(device) for t in batch]
  sent_id, mask, labels = batch
  # Get gold labels
  test_targets.extend(labels.detach().cpu().numpy())
  # Get input words
  test_inputs.append(bert_tokenizer.convert_ids_to_tokens(sent_id.detach().cpu().numpy()[0]))
  with torch.no_grad():
    # Get predictions
    outputs = model_e(sent_id, attention_mask=mask)
    # Apply softmax to the outputs
    output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
    # Get the with the highest probability as the predicted label
    test_predictions.extend(np.argmax(output_probs, axis=1))
    # Get attention weights
    # Attention weights from all layers are returned in a tuple
    # The weights from each layer are in a tensor with shape (batch_size, attention_heads, max_len, max_len)
    test_attentions.append(outputs.attentions)

#### Evaluate

In [19]:
print("F1:", f1_score(test_targets, test_predictions, average="binary"))
print("ACC:", accuracy_score(test_targets, test_predictions))
print("AUPR:", average_precision_score(test_targets, test_predictions))
print("PRECISION:", precision_score(test_targets, test_predictions))
print("RECALL:", recall_score(test_targets, test_predictions))
print("AUC:", roc_auc_score(test_targets, test_predictions))

F1: 0.9312977099236641
ACC: 0.9379310344827586
AUPR: 0.894952174262519
PRECISION: 0.9242424242424242
RECALL: 0.9384615384615385
AUC: 0.9379807692307692


## Attention analysis


In [20]:
# Get attention heatmaps
import matplotlib
from IPython.core.display import display, HTML
def colorize(words, color_array):
    cmap=matplotlib.cm.Reds
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

In [21]:
#max pooling to generate a fixed sized sentence embedding


#Max Pooling - Take the max value over time for every dimension
def max_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    max_over_time = torch.max(token_embeddings, 1)[0]
    return max_over_time

def avg_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    avg_over_time = torch.mean(token_embeddings, 1)[0]
    return avg_over_time


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other.']

#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)

#Perform pooling. In this case, max pooling
sentence_embeddings = max_pooling(model_output, encoded_input['attention_mask'])
#avg_sentence_embeddings = avg_pooling(model_output, encoded_input['attention_mask'])


print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([0.0774, 0.0319, 0.2602, 0.0943, 0.4257, 0.9204], device='cuda:0')


In [22]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([0.0774, 0.0319, 0.2602, 0.0943, 0.4257, 0.9204]): 5


In [23]:
#CLS token of each input represents the sentence embedding


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other']


#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)
    #model_output = model_output.to(device)
    
sentence_embeddings = model_output[0][:,0] #Take the first token ([CLS]) from each sentence 

print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([-0.1941,  0.0319,  0.2602,  0.0943,  0.4257,  0.2574], device='cuda:0')


In [24]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([-0.1941,  0.0319,  0.2602,  0.0943,  0.4257,  0.2574]): 4


#### What does the CLS token attend to?




In [25]:
# Original Loop

# Select some sentences randomly
sent_index = [0, 1, 2]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
    

Output hidden; open in https://colab.research.google.com to view.

In [26]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2,3,4,5,6,7,8,9,10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 3.3173e-02,  1.3241e-02,  2.0042e-01, -1.3742e-02,  5.0742e-02,
         1.1194e+00,  2.1790e-01,  3.3441e-01,  4.7600e-01,  6.8550e-01,
         3.5810e-02,  1.7075e-01,  5.7291e-02, -7.6728e-02,  8.5365e-02,
         5.0742e-02,  1.1194e+00, -2.1220e-02,  2.7198e-01,  3.0295e-02,
         8.2871e-02,  1.2012e-01,  8.6283e-02,  1.0056e-02,  2.0042e-01,
        -1.8481e-02,  5.0742e-02,  5.2506e-02,  9.0812e-02,  6.0246e-01,
         4.3039e-01,  1.2945e-01,  5.2506e-02,  2.6615e-01,  2.9773e-01,
         6.2249e-01,  8.6283e-02,  8.6060e-01,  3.2138e-01, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -1.0000e+09,  7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  1.3241e-02,  2.0042e-01, -1.3742e-02,  5.0742e-02,
         1.1194e+00,  2.1790e-01,  3.3441e-01,  4.7600e-01,  6.8550e-01,
         3.5810e-02,  1.7075e-01,  5.7291e-02, -7.6728e-02,  8.5365e-02,
         5.0742e-02,  1.1194e+00, -2.1220e-02,  2.7198e-01,  3.0295e-02,
         8.2871e-02,  1.2012e-01,  8.6283e-02,  1.0056e-02,  2.0042e-01,
        -1.8481e-02,  5.0742e-02,  5.2506e-02,  9.0812e-02,  6.0246e-01,
         4.3039e-01,  1.2945e-01,  5.2506e-02,  2.6615e-01,  2.9773e-01,
         6.2249e-01,  8.6283e-02,  8.6060e-01,  3.2138e-01, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -1.0000e+09,  7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  1.3241e-02,  2.0042e-01, -1.3742e-02,  5.0742e-02,
         1.1194e+00,  2.1790e-01,  3.3441e-01,  4.7600e-01,  6.8550e-01,
         3.5810e-02,  1.7075e-01,  5.7291e-02, -7.6728e-02,  8.5365e-02,
         5.0742e-02,  1.1194e+00, -2.1220e-02,  2.7198e-01,  3.0295e-02,
         8.2871e-02,  1.2012e-01,  8.6283e-02,  1.0056e-02,  2.0042e-01,
        -1.8481e-02,  5.0742e-02,  5.2506e-02,  9.0812e-02,  6.0246e-01,
         4.3039e-01,  1.2945e-01,  5.2506e-02,  2.6615e-01,  2.9773e-01,
         6.2249e-01,  8.6283e-02,  8.6060e-01,  3.2138e-01, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -1.0000e+09,  7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  1.3241e-02,  2.0042e-01, -1.3742e-02,  5.0742e-02,
         1.1194e+00,  2.1790e-01,  3.3441e-01,  4.7600e-01,  6.8550e-01,
         3.5810e-02,  1.7075e-01,  5.7291e-02, -7.6728e-02,  8.5365e-02,
         5.0742e-02,  1.1194e+00, -2.1220e-02,  2.7198e-01,  3.0295e-02,
         8.2871e-02,  1.2012e-01,  8.6283e-02,  1.0056e-02,  2.0042e-01,
        -1.8481e-02,  5.0742e-02,  5.2506e-02,  9.0812e-02,  6.0246e-01,
         4.3039e-01,  1.2945e-01,  5.2506e-02,  2.6615e-01,  2.9773e-01,
         6.2249e-01,  8.6283e-02,  8.6060e-01,  3.2138e-01, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -1.0000e+09,  7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

...

Tokens embeddings:
tensor([ 3.3173e-02, -6.8531e-03,  8.5674e-02,  1.7762e-01,  5.6638e-01,
         5.2340e-01,  1.4715e-01,  9.3092e-02,  5.1679e-01,  1.2012e-01,
         2.5795e-01, -3.1702e-02,  2.4864e-02, -2.3533e-02,  8.6283e-02,
         3.6311e-02,  2.5204e-02,  4.7042e-01,  5.1363e-02,  9.9946e-02,
         3.1037e-01,  8.9674e-02,  5.0742e-02,  1.1194e+00,  3.1000e-01,
        -1.0877e-02,  3.6829e-02,  2.6615e-01,  1.7075e-01, -1.0000e+09,
         6.0246e-01,  2.6615e-01,  1.0403e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -6.8531e-03,  8.5674e-02,  1.7762e-01,  5.6638e-01,
         5.2340e-01,  1.4715e-01,  9.3092e-02,  5.1679e-01,  1.2012e-01,
         2.5795e-01, -3.1702e-02,  2.4864e-02, -2.3533e-02,  8.6283e-02,
         3.6311e-02,  2.5204e-02,  4.7042e-01,  5.1363e-02,  9.9946e-02,
         3.1037e-01,  8.9674e-02,  5.0742e-02,  1.1194e+00,  3.1000e-01,
        -1.0877e-02,  3.6829e-02,  2.6615e-01,  1.7075e-01, -1.0000e+09,
         6.0246e-01,  2.6615e-01,  1.0403e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -6.8531e-03,  8.5674e-02,  1.7762e-01,  5.6638e-01,
         5.2340e-01,  1.4715e-01,  9.3092e-02,  5.1679e-01,  1.2012e-01,
         2.5795e-01, -3.1702e-02,  2.4864e-02, -2.3533e-02,  8.6283e-02,
         3.6311e-02,  2.5204e-02,  4.7042e-01,  5.1363e-02,  9.9946e-02,
         3.1037e-01,  8.9674e-02,  5.0742e-02,  1.1194e+00,  3.1000e-01,
        -1.0877e-02,  3.6829e-02,  2.6615e-01,  1.7075e-01, -1.0000e+09,
         6.0246e-01,  2.6615e-01,  1.0403e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -6.8531e-03,  8.5674e-02,  1.7762e-01,  5.6638e-01,
         5.2340e-01,  1.4715e-01,  9.3092e-02,  5.1679e-01,  1.2012e-01,
         2.5795e-01, -3.1702e-02,  2.4864e-02, -2.3533e-02,  8.6283e-02,
         3.6311e-02,  2.5204e-02,  4.7042e-01,  5.1363e-02,  9.9946e-02,
         3.1037e-01,  8.9674e-02,  5.0742e-02,  1.1194e+00,  3.1000e-01,
        -1.0877e-02,  3.6829e-02,  2.6615e-01,  1.7075e-01, -1.0000e+09,
         6.0246e-01,  2.6615e-01,  1.0403e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -6.8531e-03,  8.5674e-02,  1.7762e-01,  5.6638e-01,
         5.2340e-01,  1.4715e-01,  9.3092e-02,  5.1679e-01,  1.2012e-01,
         2.5795e-01, -3.1702e-02,  2.4864e-02, -2.3533e-02,  8.6283e-02,
         3.6311e-02,  2.5204e-02,  4.7042e-01,  5.1363e-02,  9.9946e-02,
         3.1037e-01,  8.9674e-02,  5.0742e-02,  1.1194e+00,  3.1000e-01,
        -1.0877e-02,  3.6829e-02,  2.6615e-01,  1.7075e-01, -1.0000e+09,
         6.0246e-01,  2.6615e-01,  1.0403e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

In [27]:
# Select some sentences randomly
sent_index = [11,12,13,14,15,16,17,18,19,20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 3.3173e-02,  4.1790e-01,  7.7364e-02, -3.0985e-02,  5.0742e-02,
         8.6226e-01,  6.1239e-02,  2.6615e-01,  7.5485e-02,  2.3997e-01,
         6.4561e-01,  1.1841e-01,  1.5532e-01,  5.8823e-02,  8.9582e-02,
         4.1413e-03,  1.0710e-01,  1.0359e-01,  6.0246e-01,  9.0632e-03,
         7.8163e-02, -1.8067e-02,  1.8976e-01,  9.4834e-02,  2.4700e-01,
         1.5038e-01,  2.8950e-02,  1.6537e-02,  1.1194e+00, -2.7676e-02,
         5.8310e-02, -6.7728e-02,  8.6060e-01,  6.0246e-01,  1.5389e-01,
        -4.1591e-02, -7.5124e-03, -2.8679e-02,  8.6793e-02,  8.6060e-01,
         5.5468e-02,  1.2260e-01,  6.3631e-02, -2.4761e-03,  2.6615e-01,
         1.4651e-01,  2.9773e-01,  1.2796e-02,  4.4977e-01, -4.8438e-02,
         8.9918e-02,  2.2343e-01,  2.6615e-01,  3.3842e-03,  5.0742e-02,
        -2.7676e-02,  8.6060e-01,  3.2138e-01,  7.7928e-02, -1.0000e+09,
         7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  4.1790e-01,  7.7364e-02, -3.0985e-02,  5.0742e-02,
         8.6226e-01,  6.1239e-02,  2.6615e-01,  7.5485e-02,  2.3997e-01,
         6.4561e-01,  1.1841e-01,  1.5532e-01,  5.8823e-02,  8.9582e-02,
         4.1413e-03,  1.0710e-01,  1.0359e-01,  6.0246e-01,  9.0632e-03,
         7.8163e-02, -1.8067e-02,  1.8976e-01,  9.4834e-02,  2.4700e-01,
         1.5038e-01,  2.8950e-02,  1.6537e-02,  1.1194e+00, -2.7676e-02,
         5.8310e-02, -6.7728e-02,  8.6060e-01,  6.0246e-01,  1.5389e-01,
        -4.1591e-02, -7.5124e-03, -2.8679e-02,  8.6793e-02,  8.6060e-01,
         5.5468e-02,  1.2260e-01,  6.3631e-02, -2.4761e-03,  2.6615e-01,
         1.4651e-01,  2.9773e-01,  1.2796e-02,  4.4977e-01, -4.8438e-02,
         8.9918e-02,  2.2343e-01,  2.6615e-01,  3.3842e-03,  5.0742e-02,
        -2.7676e-02,  8.6060e-01,  3.2138e-01,  7.7928e-02, -1.0000e+09,
         7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  4.1790e-01,  7.7364e-02, -3.0985e-02,  5.0742e-02,
         8.6226e-01,  6.1239e-02,  2.6615e-01,  7.5485e-02,  2.3997e-01,
         6.4561e-01,  1.1841e-01,  1.5532e-01,  5.8823e-02,  8.9582e-02,
         4.1413e-03,  1.0710e-01,  1.0359e-01,  6.0246e-01,  9.0632e-03,
         7.8163e-02, -1.8067e-02,  1.8976e-01,  9.4834e-02,  2.4700e-01,
         1.5038e-01,  2.8950e-02,  1.6537e-02,  1.1194e+00, -2.7676e-02,
         5.8310e-02, -6.7728e-02,  8.6060e-01,  6.0246e-01,  1.5389e-01,
        -4.1591e-02, -7.5124e-03, -2.8679e-02,  8.6793e-02,  8.6060e-01,
         5.5468e-02,  1.2260e-01,  6.3631e-02, -2.4761e-03,  2.6615e-01,
         1.4651e-01,  2.9773e-01,  1.2796e-02,  4.4977e-01, -4.8438e-02,
         8.9918e-02,  2.2343e-01,  2.6615e-01,  3.3842e-03,  5.0742e-02,
        -2.7676e-02,  8.6060e-01,  3.2138e-01,  7.7928e-02, -1.0000e+09,
         7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02,  4.1790e-01,  7.7364e-02, -3.0985e-02,  5.0742e-02,
         8.6226e-01,  6.1239e-02,  2.6615e-01,  7.5485e-02,  2.3997e-01,
         6.4561e-01,  1.1841e-01,  1.5532e-01,  5.8823e-02,  8.9582e-02,
         4.1413e-03,  1.0710e-01,  1.0359e-01,  6.0246e-01,  9.0632e-03,
         7.8163e-02, -1.8067e-02,  1.8976e-01,  9.4834e-02,  2.4700e-01,
         1.5038e-01,  2.8950e-02,  1.6537e-02,  1.1194e+00, -2.7676e-02,
         5.8310e-02, -6.7728e-02,  8.6060e-01,  6.0246e-01,  1.5389e-01,
        -4.1591e-02, -7.5124e-03, -2.8679e-02,  8.6793e-02,  8.6060e-01,
         5.5468e-02,  1.2260e-01,  6.3631e-02, -2.4761e-03,  2.6615e-01,
         1.4651e-01,  2.9773e-01,  1.2796e-02,  4.4977e-01, -4.8438e-02,
         8.9918e-02,  2.2343e-01,  2.6615e-01,  3.3842e-03,  5.0742e-02,
        -2.7676e-02,  8.6060e-01,  3.2138e-01,  7.7928e-02, -1.0000e+09,
         7.7928e-02,  7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02

...

Tokens embeddings:
tensor([ 3.3173e-02, -5.4577e-02,  1.7344e-01,  8.4271e-02,  8.4989e-02,
         9.4834e-02,  8.5185e-02,  1.6863e-01,  1.5425e-01, -2.4761e-03,
         1.2945e-01,  2.4700e-01,  1.6521e-01, -1.5069e-02,  6.6274e-01,
         3.1585e-01,  8.2345e-02,  7.2337e-02,  4.8633e-03,  5.8823e-02,
         2.9773e-01, -1.5537e-02,  7.3201e-02,  6.0246e-01,  7.7950e-02,
         2.5623e-01,  4.2367e-01,  1.4934e-02,  8.6283e-02,  1.0056e-02,
         7.5139e-02,  1.5625e-01,  1.4351e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -1.0000e+09,  7.7928e-02,  7.7928e-02,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -5.4577e-02,  1.7344e-01,  8.4271e-02,  8.4989e-02,
         9.4834e-02,  8.5185e-02,  1.6863e-01,  1.5425e-01, -2.4761e-03,
         1.2945e-01,  2.4700e-01,  1.6521e-01, -1.5069e-02,  6.6274e-01,
         3.1585e-01,  8.2345e-02,  7.2337e-02,  4.8633e-03,  5.8823e-02,
         2.9773e-01, -1.5537e-02,  7.3201e-02,  6.0246e-01,  7.7950e-02,
         2.5623e-01,  4.2367e-01,  1.4934e-02,  8.6283e-02,  1.0056e-02,
         7.5139e-02,  1.5625e-01,  1.4351e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -1.0000e+09,  7.7928e-02,  7.7928e-02,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -5.4577e-02,  1.7344e-01,  8.4271e-02,  8.4989e-02,
         9.4834e-02,  8.5185e-02,  1.6863e-01,  1.5425e-01, -2.4761e-03,
         1.2945e-01,  2.4700e-01,  1.6521e-01, -1.5069e-02,  6.6274e-01,
         3.1585e-01,  8.2345e-02,  7.2337e-02,  4.8633e-03,  5.8823e-02,
         2.9773e-01, -1.5537e-02,  7.3201e-02,  6.0246e-01,  7.7950e-02,
         2.5623e-01,  4.2367e-01,  1.4934e-02,  8.6283e-02,  1.0056e-02,
         7.5139e-02,  1.5625e-01,  1.4351e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -1.0000e+09,  7.7928e-02,  7.7928e-02,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -5.4577e-02,  1.7344e-01,  8.4271e-02,  8.4989e-02,
         9.4834e-02,  8.5185e-02,  1.6863e-01,  1.5425e-01, -2.4761e-03,
         1.2945e-01,  2.4700e-01,  1.6521e-01, -1.5069e-02,  6.6274e-01,
         3.1585e-01,  8.2345e-02,  7.2337e-02,  4.8633e-03,  5.8823e-02,
         2.9773e-01, -1.5537e-02,  7.3201e-02,  6.0246e-01,  7.7950e-02,
         2.5623e-01,  4.2367e-01,  1.4934e-02,  8.6283e-02,  1.0056e-02,
         7.5139e-02,  1.5625e-01,  1.4351e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -1.0000e+09,  7.7928e-02,  7.7928e-02,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

Tokens embeddings:
tensor([ 3.3173e-02, -5.4577e-02,  1.7344e-01,  8.4271e-02,  8.4989e-02,
         9.4834e-02,  8.5185e-02,  1.6863e-01,  1.5425e-01, -2.4761e-03,
         1.2945e-01,  2.4700e-01,  1.6521e-01, -1.5069e-02,  6.6274e-01,
         3.1585e-01,  8.2345e-02,  7.2337e-02,  4.8633e-03,  5.8823e-02,
         2.9773e-01, -1.5537e-02,  7.3201e-02,  6.0246e-01,  7.7950e-02,
         2.5623e-01,  4.2367e-01,  1.4934e-02,  8.6283e-02,  1.0056e-02,
         7.5139e-02,  1.5625e-01,  1.4351e-01, -2.7676e-02,  8.6060e-01,
         3.2138e-01,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
         7.7928e-02,  7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02, -1.0000e+09,  7.7928e-02,  7.7928e-02,
         7.7928e-02, -2.1756e-03,  7.7928e-02, -2.1756e-03,  7.7928e-02,
        -2.1756e-03,  7.7928e-02

In [28]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

In [29]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
      encoded_tokens = encoded_tokens.to(device)
      with torch.no_grad():
        model_output1 = model_e(**encoded_tokens)
        tokens_embeddings = model_output1[0][:,0]
        tokens_embeddings = tokens_embeddings.cpu()
        cls_attentions = head[0]
        display(HTML(colorize(tokens, cls_attentions)))
        print("Tokens embeddings:")
        print(tokens_embeddings)
        arg = argmax(tokens_embeddings)
        print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

In [30]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.0274,  0.0132,  0.2004, -0.0137, -0.0022,  1.1194,  0.2179,  0.3344,
         0.4760,  0.6855,  0.0358,  0.1708, -0.0131, -0.0767, -0.0202, -0.0022,
         1.1194, -0.0212,  0.2720,  0.0303, -0.0185,  0.1201, -0.0277,  0.0101,
         0.2004, -0.0185, -0.0022,  0.0525,  0.0908,  0.6025,  0.4304,  0.1294,
         0.0525,  0.2662,  0.2977,  0.6225, -0.0277,  0.8606,  0.3214, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.0132,  0.2004, -

Tokens embeddings:
tensor([ 0.0274,  0.0132,  0.2004, -0.0137, -0.0022,  1.1194,  0.2179,  0.3344,
         0.4760,  0.6855,  0.0358,  0.1708, -0.0131, -0.0767, -0.0202, -0.0022,
         1.1194, -0.0212,  0.2720,  0.0303, -0.0185,  0.1201, -0.0277,  0.0101,
         0.2004, -0.0185, -0.0022,  0.0525,  0.0908,  0.6025,  0.4304,  0.1294,
         0.0525,  0.2662,  0.2977,  0.6225, -0.0277,  0.8606,  0.3214, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.0132,  0.2004, -

Tokens embeddings:
tensor([ 0.0274,  0.0132,  0.2004, -0.0137, -0.0022,  1.1194,  0.2179,  0.3344,
         0.4760,  0.6855,  0.0358,  0.1708, -0.0131, -0.0767, -0.0202, -0.0022,
         1.1194, -0.0212,  0.2720,  0.0303, -0.0185,  0.1201, -0.0277,  0.0101,
         0.2004, -0.0185, -0.0022,  0.0525,  0.0908,  0.6025,  0.4304,  0.1294,
         0.0525,  0.2662,  0.2977,  0.6225, -0.0277,  0.8606,  0.3214, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.0132,  0.2004, -

Tokens embeddings:
tensor([ 0.0274,  0.0132,  0.2004, -0.0137, -0.0022,  1.1194,  0.2179,  0.3344,
         0.4760,  0.6855,  0.0358,  0.1708, -0.0131, -0.0767, -0.0202, -0.0022,
         1.1194, -0.0212,  0.2720,  0.0303, -0.0185,  0.1201, -0.0277,  0.0101,
         0.2004, -0.0185, -0.0022,  0.0525,  0.0908,  0.6025,  0.4304,  0.1294,
         0.0525,  0.2662,  0.2977,  0.6225, -0.0277,  0.8606,  0.3214, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.0132,  0.2004, -

...

Tokens embeddings:
tensor([ 0.0274, -0.0069, -0.0215,  0.1776,  0.5664,  0.5234,  0.1472,  0.0931,
         0.5168,  0.1201,  0.2579, -0.0317, -0.0019, -0.0235, -0.0277,  0.0101,
         0.0252,  0.4704, -0.0407,  0.0999,  0.3104,  0.0897, -0.0022,  1.1194,
         0.3100, -0.0109,  0.0165,  0.2662,  0.1708,  0.0316,  0.6025,  0.2662,
        -0.1396, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0069, -0.0215,  

Tokens embeddings:
tensor([ 0.0274, -0.0069, -0.0215,  0.1776,  0.5664,  0.5234,  0.1472,  0.0931,
         0.5168,  0.1201,  0.2579, -0.0317, -0.0019, -0.0235, -0.0277,  0.0101,
         0.0252,  0.4704, -0.0407,  0.0999,  0.3104,  0.0897, -0.0022,  1.1194,
         0.3100, -0.0109,  0.0165,  0.2662,  0.1708,  0.0316,  0.6025,  0.2662,
        -0.1396, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0069, -0.0215,  

Tokens embeddings:
tensor([ 0.0274, -0.0069, -0.0215,  0.1776,  0.5664,  0.5234,  0.1472,  0.0931,
         0.5168,  0.1201,  0.2579, -0.0317, -0.0019, -0.0235, -0.0277,  0.0101,
         0.0252,  0.4704, -0.0407,  0.0999,  0.3104,  0.0897, -0.0022,  1.1194,
         0.3100, -0.0109,  0.0165,  0.2662,  0.1708,  0.0316,  0.6025,  0.2662,
        -0.1396, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0069, -0.0215,  

Tokens embeddings:
tensor([ 0.0274, -0.0069, -0.0215,  0.1776,  0.5664,  0.5234,  0.1472,  0.0931,
         0.5168,  0.1201,  0.2579, -0.0317, -0.0019, -0.0235, -0.0277,  0.0101,
         0.0252,  0.4704, -0.0407,  0.0999,  0.3104,  0.0897, -0.0022,  1.1194,
         0.3100, -0.0109,  0.0165,  0.2662,  0.1708,  0.0316,  0.6025,  0.2662,
        -0.1396, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0069, -0.0215,  

Tokens embeddings:
tensor([ 0.0274, -0.0069, -0.0215,  0.1776,  0.5664,  0.5234,  0.1472,  0.0931,
         0.5168,  0.1201,  0.2579, -0.0317, -0.0019, -0.0235, -0.0277,  0.0101,
         0.0252,  0.4704, -0.0407,  0.0999,  0.3104,  0.0897, -0.0022,  1.1194,
         0.3100, -0.0109,  0.0165,  0.2662,  0.1708,  0.0316,  0.6025,  0.2662,
        -0.1396, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0069, -0.0215,  

In [31]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 0.0274,  0.4179, -0.1941, -0.0310, -0.0022,  0.8623, -0.0025,  0.2662,
        -0.0137,  0.2400,  0.6456,  0.1184,  0.1553,  0.0588, -0.0636,  0.0041,
        -0.0771,  0.1036,  0.6025,  0.0091, -0.0336, -0.0181,  0.1898,  0.0948,
         0.2470,  0.1504,  0.0079,  0.0165,  1.1194, -0.0277, -0.0031, -0.0677,
         0.8606,  0.6025,  0.1539, -0.0416, -0.0075, -0.0287, -0.0677,  0.8606,
         0.0555,  0.1226, -0.0060, -0.0025,  0.2662,  0.1465,  0.2977,  0.0128,
         0.4498, -0.0484, -0.0769,  0.2234,  0.2662,  0.0034, -0.0022, -0.0277,
         0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.4179, -0.1941, -

Tokens embeddings:
tensor([ 0.0274,  0.4179, -0.1941, -0.0310, -0.0022,  0.8623, -0.0025,  0.2662,
        -0.0137,  0.2400,  0.6456,  0.1184,  0.1553,  0.0588, -0.0636,  0.0041,
        -0.0771,  0.1036,  0.6025,  0.0091, -0.0336, -0.0181,  0.1898,  0.0948,
         0.2470,  0.1504,  0.0079,  0.0165,  1.1194, -0.0277, -0.0031, -0.0677,
         0.8606,  0.6025,  0.1539, -0.0416, -0.0075, -0.0287, -0.0677,  0.8606,
         0.0555,  0.1226, -0.0060, -0.0025,  0.2662,  0.1465,  0.2977,  0.0128,
         0.4498, -0.0484, -0.0769,  0.2234,  0.2662,  0.0034, -0.0022, -0.0277,
         0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.4179, -0.1941, -

Tokens embeddings:
tensor([ 0.0274,  0.4179, -0.1941, -0.0310, -0.0022,  0.8623, -0.0025,  0.2662,
        -0.0137,  0.2400,  0.6456,  0.1184,  0.1553,  0.0588, -0.0636,  0.0041,
        -0.0771,  0.1036,  0.6025,  0.0091, -0.0336, -0.0181,  0.1898,  0.0948,
         0.2470,  0.1504,  0.0079,  0.0165,  1.1194, -0.0277, -0.0031, -0.0677,
         0.8606,  0.6025,  0.1539, -0.0416, -0.0075, -0.0287, -0.0677,  0.8606,
         0.0555,  0.1226, -0.0060, -0.0025,  0.2662,  0.1465,  0.2977,  0.0128,
         0.4498, -0.0484, -0.0769,  0.2234,  0.2662,  0.0034, -0.0022, -0.0277,
         0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.4179, -0.1941, -

Tokens embeddings:
tensor([ 0.0274,  0.4179, -0.1941, -0.0310, -0.0022,  0.8623, -0.0025,  0.2662,
        -0.0137,  0.2400,  0.6456,  0.1184,  0.1553,  0.0588, -0.0636,  0.0041,
        -0.0771,  0.1036,  0.6025,  0.0091, -0.0336, -0.0181,  0.1898,  0.0948,
         0.2470,  0.1504,  0.0079,  0.0165,  1.1194, -0.0277, -0.0031, -0.0677,
         0.8606,  0.6025,  0.1539, -0.0416, -0.0075, -0.0287, -0.0677,  0.8606,
         0.0555,  0.1226, -0.0060, -0.0025,  0.2662,  0.1465,  0.2977,  0.0128,
         0.4498, -0.0484, -0.0769,  0.2234,  0.2662,  0.0034, -0.0022, -0.0277,
         0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274,  0.4179, -0.1941, -

...

Tokens embeddings:
tensor([ 0.0274, -0.0546,  0.1734,  0.0843, -0.0276,  0.0948, -0.0229,  0.1686,
         0.1542, -0.0025,  0.1294,  0.2470,  0.1652, -0.0151,  0.6627,  0.3158,
        -0.0185,  0.0723,  0.0049,  0.0588,  0.2977, -0.0155,  0.0732,  0.6025,
         0.0779,  0.2562,  0.4237,  0.0149, -0.0277,  0.0101, -0.0198,  0.1562,
         0.1435, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0546,  0.1734,  

Tokens embeddings:
tensor([ 0.0274, -0.0546,  0.1734,  0.0843, -0.0276,  0.0948, -0.0229,  0.1686,
         0.1542, -0.0025,  0.1294,  0.2470,  0.1652, -0.0151,  0.6627,  0.3158,
        -0.0185,  0.0723,  0.0049,  0.0588,  0.2977, -0.0155,  0.0732,  0.6025,
         0.0779,  0.2562,  0.4237,  0.0149, -0.0277,  0.0101, -0.0198,  0.1562,
         0.1435, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0546,  0.1734,  

Tokens embeddings:
tensor([ 0.0274, -0.0546,  0.1734,  0.0843, -0.0276,  0.0948, -0.0229,  0.1686,
         0.1542, -0.0025,  0.1294,  0.2470,  0.1652, -0.0151,  0.6627,  0.3158,
        -0.0185,  0.0723,  0.0049,  0.0588,  0.2977, -0.0155,  0.0732,  0.6025,
         0.0779,  0.2562,  0.4237,  0.0149, -0.0277,  0.0101, -0.0198,  0.1562,
         0.1435, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0546,  0.1734,  

Tokens embeddings:
tensor([ 0.0274, -0.0546,  0.1734,  0.0843, -0.0276,  0.0948, -0.0229,  0.1686,
         0.1542, -0.0025,  0.1294,  0.2470,  0.1652, -0.0151,  0.6627,  0.3158,
        -0.0185,  0.0723,  0.0049,  0.0588,  0.2977, -0.0155,  0.0732,  0.6025,
         0.0779,  0.2562,  0.4237,  0.0149, -0.0277,  0.0101, -0.0198,  0.1562,
         0.1435, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0546,  0.1734,  

Tokens embeddings:
tensor([ 0.0274, -0.0546,  0.1734,  0.0843, -0.0276,  0.0948, -0.0229,  0.1686,
         0.1542, -0.0025,  0.1294,  0.2470,  0.1652, -0.0151,  0.6627,  0.3158,
        -0.0185,  0.0723,  0.0049,  0.0588,  0.2977, -0.0155,  0.0732,  0.6025,
         0.0779,  0.2562,  0.4237,  0.0149, -0.0277,  0.0101, -0.0198,  0.1562,
         0.1435, -0.0277,  0.8606,  0.3214, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022, -0.0022,
        -0.0022, -0.0022, -0.0022, -0.0022, -0.0022])
arg max of tensor([ 0.0274, -0.0546,  0.1734,  

In [32]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

#### Visualize attentions for specific types of grammatical errors

In [33]:
# Lack of Subject-Verb Agreement
sentence1 = "I wrestled with this decision for years ."
# Pronoun Disagreement
sentence2 = "lined books are more enduring ."

In [34]:
# Encode the first sentence
encoded_sentence1 = bert_tokenizer.batch_encode_plus([sentence1], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence1["input_ids"]).to(device)
att = torch.tensor(encoded_sentence1["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

In [35]:
# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence1, ":", predictions[0])

I wrestled with this decision for years . : 1


In [36]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12


In [37]:
# Encode the second sentence
encoded_sentence2 = bert_tokenizer.batch_encode_plus([sentence2], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence2["input_ids"]).to(device)
att = torch.tensor(encoded_sentence2["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence2, ":", predictions[0])

lined books are more enduring . : 0


In [38]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12
